# Defining and Training the Deep Learning Surrogate Models

For the paper, we left multiple hyperparameters variable and optimized them using Google Cloud Compute and Keras Tuner. Below is code to define and train the models described in the paper. The trained model checkpoints are also provided in the repository.

Table of Contents:
* [Step 1: Import Needed Python Packages](#step1)
* [Step 2: Import and renormalize Data](#step2)
* [Step 3: Define Model and Optimize Hyperparameters](#step3)

### Step1: Import Python Packages <a class="anchor" id="step1"></a>

In [6]:
import numpy as np
from tensorflow import keras
from sklearn.model_selection import train_test_split
from keras_tuner import BayesianOptimization
import keras_tuner
import datetime
import pandas as pd
import tqdm

### Step 2: Import Data and Renormalize to [0,1] <a class="anchor" id="step2"></a>

In [7]:
# Load Data
data_URL = "../../liquid-jet-data/fulldata-inputoutput-H.csv"

# important: Check whether the index is imported as one column as well.
# If an index column is imported, set lower boundary of usecols to 1.

data = pd.read_csv(data_URL, usecols=np.arange(1, 117), index_col=False)

# # take only p polarized light:
# data = data[data['3.0']==1.]
# # drop the polarization column
# data = data.drop(['3.0'], axis=1)


# Convert data to a numpy array
data_arr = data.to_numpy()

# select only data with a0 > 1.
a0_check = True

if a0_check:
    # a0 is equivalent to Pi_4e, at column position 13; index starts at 0 (numpy)
    # (a0 should be greater 1 by construction of the simulation parameters anyway)
    data_arr = data_arr[data_arr[:, 11] > 1.0]

print("Dataset imported, size:" + str(data_arr.shape))

Dataset imported, size:(508199, 116)


We want to imagine the neural network as being a function $f$ such that for $\mathbf{x}= (E, \{\text{physical parameters}\})$, we get $f(\mathbf{x}) = \text{d}n/\text{d}E$. For that, we need to re-arrange our array.

In [8]:
x = np.zeros((100 * data_arr.shape[0], 9))

for i in tqdm.tqdm(range(data_arr.shape[0])):
    for j in range(100):
        x[int(100 * i + j)] = np.concatenate(
            (np.array([data_arr[i, -1] * j / 100]), data_arr[i, :8])
        )

100%|██████████████████████████████████████████████| 508199/508199 [01:04<00:00, 7919.74it/s]


The data is pretty big now as we can see:

In [10]:
x.shape

(50819900, 9)

We still have to normalize it. We can do that by using the maximum values we defined in the sample space.

In [11]:
# Oxygen charge
x[:, 1] = x[:, 1] / 8.0  # maximum ionization of oxygen

# Mixture
x[:, 2] = (
    x[:, 2] / 0.9
)  # 90% is always the maximum of one particle species under investigation.

# Energy
x[:, 3] = x[:, 3] / 50

# Focus-FWHM
x[:, 4] = x[:, 4] / 20e-6

# Pulse duration
x[:, 5] = x[:, 5] / 150e-15

# Incidence angle
x[:, 6] = x[:, 6] / 85

# Wavelength
x[:, 7] = x[:, 7] / 1100e-9

# Target thickness
x[:, 8] = x[:, 8] / 3e-6

In [12]:
# preparing y similarly
y = np.zeros((100 * data_arr.shape[0], 1))

for i in tqdm.tqdm(range(data_arr.shape[0])):
    for j in range(15, 115):
        y[int(100 * i + j - 15)] = data_arr[i, j]

# forcing log(0) = 0
x[x == -np.inf] = 0
y[y == -np.inf] = 0

100%|█████████████████████████████████████████████| 508199/508199 [00:16<00:00, 30897.92it/s]


(if we wanted to train the Emax model instead, we would not need to rearrange the arrays as much:)

In [ ]:
# x = dataT[:, :9]
# y = dataT[:, -1] / 2

# # for deuterons the y data has to normalized as well.
# maxY = np.min(y.flatten())
# y = y / maxY
# y = np.log10(y)

In [14]:
# Split Train, Test (Validation split is done later during training)
x_train, x_test, y_train, y_test = train_test_split(x, y, test_size=0.1)

# (we will later make 10% validation data again)
print(
    "Available data: "
    + str(len(x))
    + " data points. ("
    + str(0.9 * len(x_train))
    + " training, "
    + str(0.1 * len(x_train))
    + " validation, "
    + str(len(x_test))
    + " testing)"
)

Available data: 50819900 data points. (41164119.0 training, 4573791.0 validation, 5081990 testing)


### Step 3: Model Definition and Hyperparameter Optimization <a class="anchor" id="step3"></a>

Here, we will define a fully-connected network model which finds its best architecture and regularization using Keras Tuner. The architecture is optimized first, and then the regularization is done in the same way by using the previously determined architecture.

In [16]:
l1 = keras.regularizers.l1(l1=1e-9)
l2 = keras.regularizers.l2(l2=5e-9)

# # we can keep model checkpoints during training if we like by providing a desired output path
# savedmodel = "best_model_FullFunc_2.h5"

callbacks = [
    # keras.callbacks.ModelCheckpoint(
    #     savedmodel, save_best_only=True, monitor="val_loss"
    # ),
    tf.keras.callbacks.TensorBoard(log_dir="./logs"),
    keras.callbacks.ReduceLROnPlateau(
        monitor="val_loss", factor=0.5, patience=2, min_lr=0.0001
    ),
    keras.callbacks.EarlyStopping(monitor="val_loss", patience=3, verbose=1),
]

epochs = 1000
batch_size = 256  # can be adapted based on availabe memory. You might want to set this much higher.

In [ ]:
HPS = keras_tuner.HyperParameters()

# find best architecture
HPS.Int("num_layers", 5, 8, default=5)
for i in range(8):
    HPS.Int("units_" + str(i), min_value=128, max_value=512, step=32)


def build_model(hp):
    input_layer = keras.layers.Input(x_train.shape[1])
    layer = input_layer

    for i in range(hp.get("num_layers")):
        layer = keras.layers.Dense(units=hp.get("units_" + str(i)), activation="relu")(
            layer
        )

    output_layer = keras.layers.Dense(y_train.shape[1])(layer)

    model = keras.models.Model(inputs=input_layer, outputs=output_layer)
    model.compile(
        optimizer="adam",
        loss=keras.losses.MeanSquaredError(),
        metrics=[keras.metrics.MeanSquaredError()],
    )
    model.summary()
    return model


distribution_strategy = tf.distribute.MirroredStrategy()

tuner = BayesianOptimization(
    build_model,
    objective="val_mean_squared_error",
    hyperparameters=HPS,
    max_trials=100,
    executions_per_trial=10,
    overwrite=False,
    directory=".",
    project_name="IonOpti_2",
)

In [ ]:
tuner.search_space_summary()
tuner.search(
    x_train,
    y_train,
    batch_size=batch_size,
    epochs=epochs,
    callbacks=callbacks,
    validation_split=0.1,  # here's the 10% validation mentioned earlier
)

In [ ]:
tuner.results_summary(1)
best_model = tuner.get_best_models(1)[0]
best_hyperparameters = tuner.get_best_hyperparameters(1)[0]

# References to best trial assets
best_trial_id = tuner.oracle.get_best_trials(1)[0].trial_id
best_trial_dir = tuner.get_trial_dir(best_trial_id)

We can now save our best model if we like

In [ ]:
# best_model.save("best_model_dndE_GSCE.h5")

To obtain the best model with regularization we re-define the `build_model` function with the architecture that we found from the previous hyperparameter search:

In [ ]:
HPS.Float("l1_val", min_value=1e-9, max_value=1.0, sampling="log")
HPS.Float("l2_val", min_value=1e-9, max_value=1.0, sampling="log")

In [17]:
def build_model(hp):
    input_layer = keras.layers.Input(x_train.shape[1])
    layer = input_layer
    layer = keras.layers.Dense(
        units=320,
        activation="relu",
        kernel_regularizer=keras.regularizers.l1_l2(
            l1=hp.get("l1_val"), l2=hp.get("l2_val")
        ),
    )(layer)
    layer = keras.layers.Dense(
        units=288,
        activation="relu",
        kernel_regularizer=keras.regularizers.l1_l2(
            l1=hp.get("l1_val"), l2=hp.get("l2_val")
        ),
    )(layer)
    layer = keras.layers.Dense(
        units=288,
        activation="relu",
        kernel_regularizer=keras.regularizers.l1_l2(
            l1=hp.get("l1_val"), l2=hp.get("l2_val")
        ),
    )(layer)
    layer = keras.layers.Dense(
        units=256,
        activation="relu",
        kernel_regularizer=keras.regularizers.l1_l2(
            l1=hp.get("l1_val"), l2=hp.get("l2_val")
        ),
    )(layer)
    layer = keras.layers.Dense(
        units=256,
        activation="relu",
        kernel_regularizer=keras.regularizers.l1_l2(
            l1=hp.get("l1_val"), l2=hp.get("l2_val")
        ),
    )(layer)
    layer = keras.layers.Dense(
        units=320,
        activation="relu",
        kernel_regularizer=keras.regularizers.l1_l2(
            l1=hp.get("l1_val"), l2=hp.get("l2_val")
        ),
    )(layer)

    output_layer = keras.layers.Dense(y_train.shape[1])(layer)

    model = keras.models.Model(inputs=input_layer, outputs=output_layer)
    model.compile(
        optimizer="adam",
        loss=keras.losses.MeanSquaredError(),
        metrics=[keras.metrics.MeanSquaredError()],
    )
    model.summary()
    return model

Now we can search the same way as before

In [ ]:
tuner.search_space_summary()
tuner.search(
    x_train,
    y_train,
    batch_size=batch_size,
    epochs=epochs,
    callbacks=callbacks,
    validation_split=0.1,
)

In [ ]:
tuner.results_summary(1)
best_model = tuner.get_best_models(1)[0]
best_hyperparameters = tuner.get_best_hyperparameters(1)[0]

# References to best trial assets
best_trial_id = tuner.oracle.get_best_trials(1)[0].trial_id
best_trial_dir = tuner.get_trial_dir(best_trial_id)

Now we can save our new best model that is fully optimized:

In [ ]:
# best_model.save("best_model_dndE_GSCE.h5")

### Above we demonstrated the training of the continuous model. The training of the maximum energy model is done equivalently.